## 1.데이터 로드

In [8]:
import re
import pandas as pd
from tqdm import tqdm
from konlpy.tag import Okt
#from pykospacing import Spacing
from collections import Counter

In [9]:
import numpy as np
import pandas as pd

In [8]:
import json

with open('./naver_횟집_by_metropolitan.json','r',encoding='utf-8') as f:
    data = json.load(f)

In [9]:
#매장의 개수
len(data)

1688

In [26]:
data

{'강세호참치': {'rank': '4.49',
  'location': '서울 동대문구 천호대로 7-10 2충, 신설동역 1호선 5번 출구 50m',
  'menu': ['참치',
   '참치회',
   '어묵탕',
   '튀김',
   '생선조림',
   '순두부',
   '샐러드',
   '생선',
   '찌개',
   '순두부찌개',
   '초밥',
   '비빔밥',
   '참치비빔밥',
   '누룽지'],
  'review': ['지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요! 어묵탕 샐러드 생선조림 순두부찌개 튀김 등 곁들일수 있는 스끼다시도 같이 나와서 좋아...',
   '처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나? 벨을 눌러도 안오네요ㅋㅋ 보니까 일하 시는 분들끼리 식사중이셨네요 10시?쯤? 노래...',
   '가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알게된 강세호참치 집이에요! 5명이라 참다랑어 대자와 중자주문...',
   '일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐거에요 첨 포장방문으로 사장님도 뵙고 우린 양많이 준...',
   '음식이 깔끔하고 맛있네요',
   '굿',
   '굿',
   '신설동에 진짜 괜찮은 맛집 찾기 어려운데 아빠랑 즐거운 참치 데이트 했어요 이 가격에 만족도 최상! 배달 맛집으로 이미 유명한 곳 홀에서 아늑하...',
   '네이버의 영업시간이랑 달라서 급하게 먹고 나왔습 니다! (위드 코로나시점) 가격적인 측면에서는 매우 합리적입니다! 저희가 너무 늦게 방문해서그...',
   '츰치가 증말로 맛있습니다 강추입니다',
   '참치가 정말 신선하니 맛있어요',
   '좋아요~^^',
   '맛있게 잘 먹고 갑니다',
   '구성이 아쉬웠는데 그래도 친절하시고 잘 먹었어요~',
   '11월 모임때 한번 먹어보고 기억에 남아 친구들이랑 다시 방문했습니다 역시나 참치로 배채우고 갔습니 다ㅎㅎ 가마도로 오도로

## 2. 전처리
1. 각 매장 마다의 리뷰 리스트를 나누고
2. null값 확인
3. 한글빼고 삭제
4. 중복제거
5. 레이블링

In [10]:
#1. 각 매장 마다의 리뷰 리스트를 나누고
total_review = list()
import pandas as pd
for store_info in data.values():
    total_review.extend(store_info['review'])

In [11]:
len(total_review)

155212

In [12]:
df = pd.DataFrame(total_review, columns=['Review'])

In [13]:
df

Review
0       지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요! 어묵탕 샐러드 생선조림 ...
1       처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나? 벨을 눌러도 안오네요ㅋ...
2       가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...
3       일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...
4                                           음식이 깔끔하고 맛있네요
...                                                   ...
155207                                    깨끗하고 친절해요 맘에듭니다
155208                                               친절해요
155209                                    깨끗하고 친절해요 맘에듭니다
155210                                               친절해요
155211  주인님 넘넘친절하고 확실하게하시내요 그리고 회는기계로설지안고 손은로직접설어맛이확실히...

[155212 rows x 1 columns]

In [14]:
# null값 확인
df.isnull().sum()

Review    0
dtype: int64

In [15]:
#여러 공백을 하나의 공백으로 줄인다.
import re
def apply_regular_expreesion(text):
    hangul = re.compile('[^ 가-힣]')
    #한글이 아닌 문자 제거
    result = hangul.sub('', text) 
    #1개 이상의 공백 -> 1개의 공백
    result = re.sub(' +',' ', result)
    return result

df['Review'] = df['Review'].apply(lambda x : apply_regular_expreesion(x))

In [16]:
tmp = df[df['Review']=='']
tmp

Review
29           
102          
114          
128          
130          
...       ...
155163       
155176       
155180       
155181       
155193       

[5223 rows x 1 columns]

In [17]:
#빈 문자열 -> NaN 치환
df['Review'].replace('', np.nan, inplace=True)
# null값 확인
print(df.isnull().sum())
df.dropna(inplace=True)
len(df)

Review    5223
dtype: int64


149989

In [18]:
df.duplicated(['Review']).sum()

54293

In [19]:
#중복 제거
df = df.drop_duplicates(['Review'])
print(df.duplicated(['Review']).sum())

0


In [20]:
print(df.isnull().sum())

Review    0
dtype: int64


In [21]:
len(df)

95696

In [22]:
df = df[df['Review'].map(lambda x : len(str(x)) > 10) ]

In [23]:
df = df.reset_index(drop=True)

In [27]:
df

Review
0      지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요 어묵탕 샐러드 생선조림 순...
1      처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나 벨을 눌러도 안오네요 보...
2      가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...
3      일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...
4                                          음식이 깔끔하고 맛있네요
...                                                  ...
83564                            방어 넘 양도 많고 짱이네요포장도 갠찬아요
83565                                       횟감이 신선하고 쫀득한
83566                    사장님 친절하시고 음식도맛있고 좋아요서비스도 엄청 좋아요
83567                                    깨끗하고 친절해요 맘에듭니다
83568  주인님 넘넘친절하고 확실하게하시내요 그리고 회는기계로설지안고 손은로직접설어맛이확실히...

[83569 rows x 1 columns]

In [3]:
import pickle
with open('df_tmp.pickle', 'wb') as f:
    pickle.dump(df, f)

NameError: name 'df' is not defined

In [10]:
#레이블링 하기
#현재 인덱스 3000까지 했다.
for i in range(df['Label'].count(), 3000):
    print(f'{i}번째 인덱스')
    print(df.loc[i,'Review'])
    label = input("레이블 입력하세요: ")
    label = int(label)
    df.loc[i,'Label'] = label

2993번째 인덱스
나오는 기타 요리들도 너무 맛있고 무엇보다 대게가 좋습니다 찌시는 방법도 직접 솥에 쪄주셔서 정성이 들어가 더 맛있는 것 같아요 너무 친절하셔서 
레이블 입력하세요: 1
2994번째 인덱스
너무 맛있게 잘 먹었습니다 사장님도 친절하시고 무엇보다 킹크랩이 엄청 살도 꽉차고 진짜 진짜 맛있습니다 무조건 재방문각입니다
레이블 입력하세요: 1
2995번째 인덱스
동교동 창천동 모두 먹었던 곳에서 제일 만족한 곳이에요 서비스는 물론이고 기본 채소 퀄리티부터가 정말 진짜 추천 많이합니다 기분좋아지는 것
레이블 입력하세요: 1
2996번째 인덱스
제가 사진찍는 기술이 후져서 실제 나온 것보다 못찍어서 아쉽네요 잘먹었습니다
레이블 입력하세요: 1
2997번째 인덱스
대게맛의 진수 서비스도 많고 정말 맛있습니다
레이블 입력하세요: 1
2998번째 인덱스
먹기 좋게 손쉽게 손질되어 나오고 속살도 꽉 차서 진짜 맛있게 잘 먹었습니다신선해서 그런지 비린내도 전혀 안났어요
레이블 입력하세요: 1
2999번째 인덱스
참 맛있게 먹고 갑니다
레이블 입력하세요: 1


In [96]:
df[df['Review'] == '양이 예전보다 좀 줄은 느낌적인 느낌맛있는데 아쉬웠어요']

Review  Label
1607  양이 예전보다 좀 줄은 느낌적인 느낌맛있는데 아쉬웠어요    1.0

In [11]:
df['Label'][2664] = 1

C:\Users\JSWonner\AppData\Local\Temp\ipykernel_22536\1467170492.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Label'][2664] = 1


In [83]:
df.loc[:1500,:]

Review  Label
0     지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요 어묵탕 샐러드 생선조림 순...    1.0
1     처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나 벨을 눌러도 안오네요 보...    0.0
2     가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...    1.0
3     일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...    1.0
4                                         음식이 깔끔하고 맛있네요    1.0
...                                                 ...    ...
1496  늦었지만 민어 인분 만원에 둘이 먹어도 먹어도 남아요 너무 너무 양 많고 부위도 다...    2.0
1497                  모듬회 항상 맛있게 먹는데물회도 있는지몰랐어요 물회도 맛나요    2.0
1498  노량진 수산시장의 신선한 모듬회를 인터넷으로 간 편하게 주문할 수 있으니 바쁜시간이...    1.0
1499  인짜리 포장해왔는데 너무 맛있어요 얇게 두께 선택해도 충분히 두툼하구요 물회 육수는...    1.0
1500  역시 믿고가는 형제수산 미리손질을 다 해주셔서 먹기 매우편하고 두께도 기본적으로 두...    NaN

[1501 rows x 2 columns]

In [10]:
df.value_counts(['Label']).sum()

2500

In [10]:
import pickle
with open('df_tmp.pickle', 'rb') as f:
    df = pickle.load(f)

In [11]:
df

Review  Label
0      지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요 어묵탕 샐러드 생선조림 순...    1.0
1      처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나 벨을 눌러도 안오네요 보...    0.0
2      가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...    1.0
3      일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...    1.0
4                                          음식이 깔끔하고 맛있네요    1.0
...                                                  ...    ...
83564                            방어 넘 양도 많고 짱이네요포장도 갠찬아요    NaN
83565                                       횟감이 신선하고 쫀득한    NaN
83566                    사장님 친절하시고 음식도맛있고 좋아요서비스도 엄청 좋아요    NaN
83567                                    깨끗하고 친절해요 맘에듭니다    NaN
83568  주인님 넘넘친절하고 확실하게하시내요 그리고 회는기계로설지안고 손은로직접설어맛이확실히...    NaN

[83569 rows x 2 columns]

In [16]:
import pandas as pd
import numpy as np
df.value_counts(['Label']).sum()

2500

In [32]:
tmp = df.sample(n=5000, replace = False, random_state=24)

In [33]:
tmp.count()

Review    5000
Label      150
dtype: int64

In [38]:
# 기존의 순차적 레이블링 진행했던 2500개의 레코드 df
# 새롭게 비복원 추출로 랜덤하게 뽑은 5000개 tmp를 합친다.
df = pd.concat([df.iloc[:2500,:], tmp], ignore_index=True)

In [39]:
df.count()

Review    7500
Label     2650
dtype: int64

In [41]:
# 중복제거
df.drop_duplicates(['Review'],ignore_index=True, inplace=True)
df.count()

Review    7350
Label     2500
dtype: int64

In [79]:
for i in range(df['Label'].count(), 3000):
    print(f'{i}번째 인덱스')
    print(df.loc[i,'Review'])
    label = input("레이블 입력하세요: ")
    label = int(label)
    df.loc[i,'Label'] = label

2940번째 인덱스
반찬들 하나하나 다 잘나왔어요 청어구이보다는 꽁 치가 더 좋을것 같긴 한데 방어 먹으러 왔는데 메뉴에 없는 방어참가자미 반반으로 해주셔
레이블 입력하세요: 1
2941번째 인덱스
방어우럭 포장했는데 광어우럭이 있네요 바쁠때 아니었는데 포장하기전에 확인해주시면 좋겠어요
레이블 입력하세요: 1
2942번째 인덱스
회가 너무 신선하고 맛있었어요
레이블 입력하세요: 1
2943번째 인덱스
혼밥 해서 죄송하지만 청결하고 친절하고음식도 신선하고 너무 좋아요 또갈게요
레이블 입력하세요: 1
2944번째 인덱스
위생 상태도 너무 좋고 맛있게 잘 먹었어요 그날 하 루 배가 터질 지경이었어요 상다리가 부러지게 나와서 회 상태도 너무 신선하고 좋더라
레이블 입력하세요: 1
2945번째 인덱스
항상친절하고 좋아요 노량진 갈때마다 무조건 청해진
레이블 입력하세요: 1
2946번째 인덱스
모듬회하고 물회 너무 맛있게 먹었어요초밥도 팔던데 다음에 재방문해서 먹어보려구요
레이블 입력하세요: 1
2947번째 인덱스
너무 맛있게 먹고 갓네요 서비스나 회 신선도나친절함이나 최고에요
레이블 입력하세요: 1
2948번째 인덱스
룸으로 배정 받아서 더 좋은시간 보냈네요
레이블 입력하세요: 1
2949번째 인덱스
맛있어요 점심특선 라멘은 좀 그랬어요
레이블 입력하세요: 1
2950번째 인덱스
차 차로 오는 사람들이 많다보니 많이 시끄럽고 정신이 없어요 
레이블 입력하세요: 0
2951번째 인덱스
자주가는 참치집입니다 맛 친절 양 질 다 좋아용
레이블 입력하세요: 1
2952번째 인덱스
최고였네요 싱싱하고 가성비 좋았습니다 기분 좋게 먹고 나왔어요 친구들에게도 추천하고 싶은 집입니다
레이블 입력하세요: 1
2953번째 인덱스
광어포차 좋아요친절하고 맛있어요
레이블 입력하세요: 1
2954번째 인덱스
회랑 새우튀김도 매운탕도 맛있었어요
레이블 입력하세요: 1
2955번째 인덱스
맛있고 가격도 좋아요
레이블 입력하세요: 1
2956번째 인덱스
여러가지 종류의 회와 해산물이 들어있어서 여

In [84]:
df.value_counts(['Label']).sum()

3000

In [87]:
result = df.iloc[:3000,:]
result

Review  Label
0     지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요 어묵탕 샐러드 생선조림 순...    1.0
1     처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나 벨을 눌러도 안오네요 보...    0.0
2     가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...    1.0
3     일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...    1.0
4                                         음식이 깔끔하고 맛있네요    1.0
...                                                 ...    ...
2995                                  사시미 종류도 많고 양도 좋아용    1.0
2996  절대 가지마세요 점도 못줌 성남동 관평동 용문동 에서 자주 애용하면서 체인점이라도 ...    0.0
2997                                      양도 엄청 많고 맛잇어용    1.0
2998                     너무 맛있어요 사장님도 친절하셔서 기분 좋게 먹다갑니다    1.0
2999                  을왕리 횟집 찾으시는분들 고고고 진짜 맛있습니다 가격도 좋고    1.0

[3000 rows x 2 columns]

In [93]:
result = result.astype({'Label':'int'})

In [94]:
result

Review  Label
0     지금까지 다녀봤던 참치집 중 부위가 가장 좋았던거 같아요 어묵탕 샐러드 생선조림 순...      1
1     처음 들어갈땐 사장님이 계신거같더니 먹는 중에는 퇴근하셨나 벨을 눌러도 안오네요 보...      0
2     가족들 다 참치회를 좋아해서 생일겸 맛있는 참치회 먹으려고 집근처로 찾아보던중에 알...      1
3     일등참치 맛집참치 가성비참치 최고참치 증독참치 구청뒤쪽에서 신설동으로 계속 딸라다닐...      1
4                                         음식이 깔끔하고 맛있네요      1
...                                                 ...    ...
2995                                  사시미 종류도 많고 양도 좋아용      1
2996  절대 가지마세요 점도 못줌 성남동 관평동 용문동 에서 자주 애용하면서 체인점이라도 ...      0
2997                                      양도 엄청 많고 맛잇어용      1
2998                     너무 맛있어요 사장님도 친절하셔서 기분 좋게 먹다갑니다      1
2999                  을왕리 횟집 찾으시는분들 고고고 진짜 맛있습니다 가격도 좋고      1

[3000 rows x 2 columns]

In [98]:
result['Label'].values

array([1, 0, 1, ..., 1, 1, 1])

In [101]:
drop_index = result[result['Label'] > 1].index
result.drop(drop_index,inplace=True)

In [102]:
result.reset_index(drop=True,inplace=True)

In [103]:
result.value_counts(['Label'])

Label
1        2405
0         527
dtype: int64

In [105]:
import pickle
with open('result.pickle', 'wb') as f:
    pickle.dump(result,f)